In [9]:
import gym
from gym import spaces
import numpy as np
import pandas as pd
pd.options.mode.chained_assignment = None 

import matplotlib.pyplot as plt
from stable_baselines3.common.env_checker import check_env
from stable_baselines3 import DQN
from env import get_dataset, Battery

from plot import display_profit, display_schedule

from sklearn.preprocessing import MinMaxScaler
from tqdm import tqdm



# Get dataset 

In [10]:
k = 5 
df = get_dataset()



In [11]:
df_train = df[df.timestamp.dt.year==2020].reset_index(drop=True)
df_test = df[df.timestamp.dt.year==2021].reset_index(drop=True)

scaler = MinMaxScaler()
df_train["scaled_price"] = scaler.fit_transform(df_train.price.to_numpy().reshape(-1, 1))
df_test["scaled_price"]  = scaler.transform(df_test.price.to_numpy().reshape(-1, 1))


# Get environments 

In [12]:
train_env = Battery(df_train,k=k)
test_env = Battery(df_test,k=k)

# Random policy

In [13]:
cum_reward, df_optim = test_env.test()


100%|█████████▉| 8754/8760 [00:00<00:00, 57006.27it/s]


In [14]:
display_schedule(df_optim)

In [15]:
display_profit(df_optim)

# DQN policy

In [16]:

train_env.reset()
model = DQN("MlpPolicy", train_env, verbose=1)
model.learn(total_timesteps=10000, log_interval=4)

# model.save("dqn_cartpole")
# del model # remove to demonstrate saving and loading
# model = DQN.load("dqn_cartpole")




Using cuda device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Test on train env :

In [17]:
cum_reward, df_optim = train_env.test(model)



100%|█████████▉| 8777/8783 [00:11<00:00, 747.13it/s] 


In [18]:
display_schedule(df_optim)



In [19]:
display_profit(df_optim)

## Test on test env : 

In [20]:
cum_reward, df_optim = test_env.test(model)



100%|█████████▉| 8754/8760 [00:09<00:00, 903.73it/s] 


In [21]:
display_schedule(df_optim)

In [22]:
display_profit(df_optim)